In [ ]:
!pip install requests beautifulsoup4 praw

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 191.0/191.0 kB 3.3 MB/s eta 0:00:00


In [ ]:
google_api_key = '<enter-yours>'
search_engine_id = '<enter-yours>'

reddit_client_id = '<enter-yours>'
reddit_client_secret = '<enter-yours>'
reddit_user_agent = '<enter-yours>'

In [ ]:
import requests
import praw
import json
from bs4 import BeautifulSoup
from urllib.parse import urlparse

In [ ]:
def search_google(query):
    url = f"https://www.googleapis.com/customsearch/v1?key={google_api_key}&cx={search_engine_id}&q={query}"
    response = requests.get(url)
    results = response.json().get('items', [])
    return results

# Extract subreddits maintaining order
def extract_subreddits(google_results):
    subreddits = []
    seen_subreddits = set()

    for item in google_results:
        parsed_url = urlparse(item['link'])
        if 'reddit.com' in parsed_url.netloc:
            path_parts = parsed_url.path.split('/')
            if len(path_parts) > 2 and path_parts[1] == 'r':
                subreddit = path_parts[2]
                if subreddit not in seen_subreddits:
                    subreddits.append(subreddit)
                    seen_subreddits.add(subreddit)

    return subreddits

In [ ]:
def scrape_reddit(subreddits, query):
    reddit = praw.Reddit(
        client_id=reddit_client_id,
        client_secret=reddit_client_secret,
        user_agent=reddit_user_agent
    )

    reddit_gossip = []

    for subreddit_name in subreddits:
        subreddit = reddit.subreddit(subreddit_name)
        posts = list(subreddit.search(query, limit=100))  # Retrieve up to 100 posts to sort from

        # Sort posts by upvotes and number of comments
        sorted_posts = sorted(posts, key=lambda x: (x.score, x.num_comments), reverse=True)[:20]

        for submission in sorted_posts:
            title = submission.title
            selftext = submission.selftext
            link = submission.url
            post_upvotes = submission.score  # Upvotes for the post
            comment_count = submission.num_comments  # Number of comments for the post
            comments = []

            # Extract comments
            submission.comments.replace_more(limit=0)
            for comment in submission.comments:
                comment_info = {
                    'body': comment.body,
                    'upvotes': comment.score  # Upvotes for the comment
                }
                comments.append(comment_info)

            reddit_gossip.append({
                'subreddit': subreddit_name,
                'title': title,
                'selftext': selftext,
                'link': link,
                'upvotes': post_upvotes,
                'commentcount': comment_count,
                'comments': comments
            })

    return reddit_gossip



def save_to_json(data, filename='reddit_gossip.json'):
    with open(filename, 'w') as f:
        json.dump(data, f, indent=4)

In [ ]:
# Google search query
def search_and_scrape(query):
    # Append "reddit" to the query
    gquery = query + " reddit"

    # Step 1: Search Google for relevant subreddits
    google_results = search_google(gquery)
    subreddits = extract_subreddits(google_results)
    print("Extracted subreddits:", subreddits)

    # Step 2: Scrape Reddit for gossip
    reddit_gossip = scrape_reddit(subreddits, query)

    # Step 3: Save the data to a JSON file
    save_to_json(reddit_gossip)

    print("Reddit gossip data saved to reddit_gossip.json")

# Example usage
query = input("What lore would ya like to explore today: ")
search_and_scrape(query)




What lore would ya like to explore today: Drake Kendrick feud


It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.



Extracted subreddits: ['hiphop101', 'KendrickLamar', 'Drizzy', 'ToddintheShadow', 'askTO', 'Fauxmoi']


It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/l

Reddit gossip data saved to reddit_gossip.json


In [ ]:
# Download the JSON file
from google.colab import files
files.download('reddit_gossip.json')

FileNotFoundError: Cannot find file: reddit_gossip.json

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
ls

drive/  sample_data/


In [ ]:
cd drive/MyDrive/gossipai/

/content/drive/MyDrive/gossipai


In [ ]:
from google.colab import files
files.download('reddit_gossip.json')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
import json
with open('reddit_gossip.json', 'r') as file:
    data = json.load(file)

In [ ]:

print(type(data))  # Should be a list
print(data[0].keys())  # Should print the keys of the first post

<class 'list'>
dict_keys(['subreddit', 'title', 'selftext', 'link', 'upvotes', 'commentcount', 'comments'])


In [ ]:
import re

# Helper function to clean text data
def clean_text(text):
    text = text.lower()  # Convert to lowercase
    text = re.sub(r'\s+', ' ', text)  # Remove extra spaces
    text = re.sub(r'[^\w\s]', '', text)  # Remove special characters
    return text



In [ ]:
from textblob import TextBlob

# Function to get sentiment polarity of text
def get_sentiment(text):
    analysis = TextBlob(text)
    return analysis.sentiment.polarity  # Returns polarity score between -1 (negative) and 1 (positive)


In [ ]:
# from sklearn.feature_extraction.text import CountVectorizer
# from sklearn.decomposition import LatentDirichletAllocation

# def get_topics(text, n_topics=5):
#     if not text.strip():  # Check if text is empty after stripping whitespace
#         return None

#     # Adjust CountVectorizer parameters
#     vectorizer = CountVectorizer(max_df=1, min_df=0.8, stop_words='english')
#     dtm = vectorizer.fit_transform([text])

#     # Check if document-term matrix has no features or is too sparse
#     if dtm.shape[1] == 0 or dtm.sum() == 0:
#         return []

#     # Fit LDA model
#     lda = LatentDirichletAllocation(n_components=n_topics, random_state=42)
#     lda.fit(dtm)
#     topics = lda.components_

#     return topics


In [ ]:
def weight_response(upvotes, sentiment, comment_count):
    upvote_weight = upvotes / 100.0  # Normalize upvotes (assuming scale)

    # Normalize sentiment to [-1, 1]
    sentiment_normalized = sentiment / 2.0  # Assuming sentiment ranges from -2 to 2

    # Use absolute value of sentiment to capture intensity
    sentiment_modulated = abs(sentiment_normalized)

    # Calculate weight based on comment count
    comment_weight = comment_count / 10.0  # Normalize comment count (assuming scale)

    # Combine weights
    weighted_score = upvote_weight + sentiment_modulated + comment_weight

    return weighted_score



In [ ]:
training_pairs = []

for post in data:
    # Clean the title and selftext
    post_title = clean_text(post['title'])
    post_selftext = clean_text(post['selftext'])

    # Get sentiment of title and selftext
    sentiment_title = get_sentiment(post_title)
    sentiment_selftext = get_sentiment(post_selftext)

    # Weight response for post based on upvotes, sentiment, and comment count
    post_upvotes = post.get('upvotes', 0)
    post_comment_count = len(post['comments'])  # Assuming comment count directly from post data
    weighted_score_post = weight_response(post_upvotes, sentiment_title, post_comment_count)

    # Process comments
    comments = post['comments']
    for comment in comments:
        # Clean comment body
        comment_body = clean_text(comment['body'])

        # Print comment body to inspect its content
        print("Comment Body:", comment_body)

        # Get sentiment of comment
        sentiment_comment = get_sentiment(comment_body)

        # Weight response for comment based on upvotes, sentiment, and comment count
        comment_upvotes = comment.get('upvotes', 0)
        weighted_score_comment = weight_response(comment_upvotes, sentiment_comment, 0)  # Assume comment count isn't used for comments

        # Create training pairs (or use as needed)
        training_pairs.append({
            "prompt": post_title,
            "response": comment_body,
            "weighted_score": weighted_score_comment
        })

    # Print or store results as needed
    print(f"Post Title: {post_title}")
    print(f"Post Sentiment: {sentiment_title}")
    print(f"Weighted Score (Post): {weighted_score_post}")
    print("---")


Streaming output truncated to the last 5000 lines.
Comment Body: i think personally drake had a chance if he stayed with songs like family matters just focusing on flow and his penmanship
Comment Body: shouldnt have poked the bear shouldnt have tried to outrap kendricksurprised he didnt take the route of making a clubjamfriendly diss banger like what back 2 back was against meek and what not like us was here shouldnt have spent 80 of his last response hp6 on his back foot defending himself against allegations and especially shouldnt have used the terrible if i was guilty i wouldve been caught im too famous defense
Comment Body: not been a hoe
Comment Body: he shouldve had something ready after family matters he honestly let kendrick drown him out and gain mad momentum drake cant rap as good as kendrick but hes still good enough where he couldve won if he picked the proper angle he got outplayed in basically every single way
Comment Body: kendrick bought his son up first
Comment Body: t

In [ ]:
for pair in training_pairs:
    print(pair)

Streaming output truncated to the last 5000 lines.
{'prompt': 'whats the whole beef between kendrick lamar and drake', 'response': 'can someone pls correct this fool httpswwwredditcomrunderated_songscomments1d28d1awhy_is_kendrick_lamar_so_underratedutm_sourceshareutm_mediumweb3xutm_nameweb3xcssutm_term1utm_contentshare_buttonhttpswwwredditcomrunderated_songscomments1d28d1awhy_is_kendrick_lamar_so_underratedutm_sourceshareutm_mediumweb3xutm_nameweb3xcssutm_term1utm_contentshare_button', 'weighted_score': 0.001}
{'prompt': 'whats the whole beef between kendrick lamar and drake', 'response': 'rap is in a lull someone isnt providing the energy and the industry beef shit pops up to generate interest', 'weighted_score': 0.1}
{'prompt': 'whats the whole beef between kendrick lamar and drake', 'response': 'its light skin against dark skin civil war pick a side ', 'weighted_score': 0.0625}
{'prompt': 'whats the whole beef between kendrick lamar and drake', 'response': 'i see kendrick as postrap

In [ ]:
import json

# Input data (list of dictionaries)
data = training_pairs

# Group by prompt
grouped = {}
for entry in data:
    prompt = entry["prompt"]
    if prompt not in grouped:
        grouped[prompt] = []
    grouped[prompt].append(entry)

# Generate preference pairs
preference_pairs = []
for prompt, responses in grouped.items():
    # Sort responses by weighted_score in descending order
    responses = sorted(responses, key=lambda x: x["weighted_score"], reverse=True)

    # Create pairs: higher score vs. lower score
    for i in range(len(responses)):
        for j in range(i + 1, len(responses)):
            pair = {
                "prompt": prompt,
                "response_a": responses[i]["response"],
                "response_b": responses[j]["response"],
                "label": 1  # Indicating response_a is preferred
            }
            preference_pairs.append(pair)

# Save to JSONL file
with open("preference_pairs.jsonl", "w") as f:
    for pair in preference_pairs:
        f.write(json.dumps(pair) + "\n")

print("Preference pairs saved to preference_pairs.jsonl")


Preference pairs saved to preference_pairs.jsonl


In [ ]:
for pair in preference_pairs:
    print(pair)

Streaming output truncated to the last 5000 lines.
{'prompt': 'drake canceled his lollapalooza brazil concert on the day of citing technical problems but actually never intended to perform', 'response_a': 'damn you really did twenty one pilots dirty there ', 'response_b': 'aggressive reminder that he still needs to apologize to megan thee stallion', 'label': 1}
{'prompt': 'drake canceled his lollapalooza brazil concert on the day of citing technical problems but actually never intended to perform', 'response_a': 'damn you really did twenty one pilots dirty there ', 'response_b': 'drakes conversations about coming to brazil is the lack of enthusiasm of the fans no drake its just youhttpswwwyoutubecomwatchvfmgweveaeoclistrdfmgweveaeocstart_radio1 edit  link prob', 'label': 1}
{'prompt': 'drake canceled his lollapalooza brazil concert on the day of citing technical problems but actually never intended to perform', 'response_a': 'damn you really did twenty one pilots dirty there ', 'respon

In [ ]:
for pair in preference_pairs:
    print(pair)

Streaming output truncated to the last 5000 lines.
{'prompt': 'drake canceled his lollapalooza brazil concert on the day of citing technical problems but actually never intended to perform', 'response_a': 'damn you really did twenty one pilots dirty there ', 'response_b': 'aggressive reminder that he still needs to apologize to megan thee stallion', 'label': 1}
{'prompt': 'drake canceled his lollapalooza brazil concert on the day of citing technical problems but actually never intended to perform', 'response_a': 'damn you really did twenty one pilots dirty there ', 'response_b': 'drakes conversations about coming to brazil is the lack of enthusiasm of the fans no drake its just youhttpswwwyoutubecomwatchvfmgweveaeoclistrdfmgweveaeocstart_radio1 edit  link prob', 'label': 1}
{'prompt': 'drake canceled his lollapalooza brazil concert on the day of citing technical problems but actually never intended to perform', 'response_a': 'damn you really did twenty one pilots dirty there ', 'respon

In [ ]:


!pip install -q datasets trl peft bitsandbytes sentencepiece wandb

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 26.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 293.4/293.4 kB 22.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.1/69.1 MB 11.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 9.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 15.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 16.1 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [ ]:

import os
import gc
import torch

import transformers
from transformers import AutoModelForCausalLM, AutoTokenizer, TrainingArguments, BitsAndBytesConfig
from datasets import load_dataset
from peft import LoraConfig, PeftModel, get_peft_model, prepare_model_for_kbit_training
from trl import DPOTrainer
import bitsandbytes as bnb
from google.colab import userdata
import wandb



model_name = "teknium/OpenHermes-2.5-Mistral-7B"
new_model = "NeuralHermes-2.5-Mistral-7B"

In [ ]:
# Define the chatml_format function
def chatml_format(example):
    # Define the system message
    system = "You are an AI gossiper designed to interact in the style of a human gossiper on Reddit. Analyze the euphemisms, humor, and slang in the given examples to generate well-informed yet controversial takes and opinions."

    # Format the user prompt
    message = {"role": "user", "content": example['prompt']}
    prompt = tokenizer.apply_chat_template([message], tokenize=False, add_generation_prompt=True)

    # Determine chosen and rejected based on label
    if example['label'] == 1:  # Label 1 means response_a is chosen
        chosen = example['response_a'] + "<|im_end|>\n"
        rejected = example['response_b'] + "<|im_end|>\n"
    else:  # Label 0 means response_b is chosen
        chosen = example['response_b'] + "<|im_end|>\n"
        rejected = example['response_a'] + "<|im_end|>\n"

    return {
        "prompt": system + prompt,
        "chosen": chosen,
        "rejected": rejected,
    }

tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "left"
# Format the preference_pairs dataset
formatted_dataset = [chatml_format(example) for example in preference_pairs]

# Print sample
print(formatted_dataset[1])


# Tokenizer
# model_name = "your_model_name_here"  # Replace with your model name
# tokenizer = AutoTokenizer.from_pretrained(model_name)
# tokenizer.pad_token = tokenizer.eos_token
# tokenizer.padding_side = "left"


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/1.60k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/493k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/51.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/101 [00:00<?, ?B/s]

{'prompt': 'You are an AI gossiper designed to interact in the style of a human gossiper on Reddit. Analyze the euphemisms, humor, and slang in the given examples to generate well-informed yet controversial takes and opinions.<|im_start|>user\nnow that kendrick said it everyone is like ok drake is actually a pedo<|im_end|>\n<|im_start|>assistant\n', 'chosen': 'the cops didnt take down cosby hannibal buress did<|im_end|>\n', 'rejected': 'sometimes its hard to take down our heroes remember bill cosby people knew about it for years and it took hannibal buress to joke about it to get that resolved<|im_end|>\n'}


In [ ]:
from datasets import Dataset

# Convert the formatted dataset (which is a list of dictionaries) into a datasets.Dataset
train_dataset = Dataset.from_dict({
    "prompt": [example["prompt"] for example in formatted_dataset],
    "chosen": [example["chosen"] for example in formatted_dataset],
    "rejected": [example["rejected"] for example in formatted_dataset],
})

# Now you can use this `train_dataset` in your DPOTrainer
print(train_dataset[0])

{'prompt': 'You are an AI gossiper designed to interact in the style of a human gossiper on Reddit. Analyze the euphemisms, humor, and slang in the given examples to generate well-informed yet controversial takes and opinions.<|im_start|>user\nnow that kendrick said it everyone is like ok drake is actually a pedo<|im_end|>\n<|im_start|>assistant\n', 'chosen': 'the cops didnt take down cosby hannibal buress did<|im_end|>\n', 'rejected': 'no on the kanye board people have been talking about this for years<|im_end|>\n'}


In [ ]:

# LoRA configuration
peft_config = LoraConfig(
    r=16,
    lora_alpha=16,
    lora_dropout=0.05,
    bias="none",
    task_type="CAUSAL_LM",
    target_modules=['k_proj', 'gate_proj', 'v_proj', 'up_proj', 'q_proj', 'o_proj', 'down_proj']
)

# Model to fine-tune
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    torch_dtype=torch.float16,
    load_in_4bit=True
)
model.config.use_cache = False

# Training arguments


config.json:   0%|          | 0.00/624 [00:00<?, ?B/s]

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.
`low_cpu_mem_usage` was None, now default to True since model is quantized.


model.safetensors.index.json:   0%|          | 0.00/25.1k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.94G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/4.54G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/120 [00:00<?, ?B/s]

In [ ]:
# Print model type
print(f"Model type: {type(model)}")

# Check model configuration
print(f"Model config: {model.config}")

Model type: <class 'transformers.models.mistral.modeling_mistral.MistralForCausalLM'>
Model config: MistralConfig {
  "_attn_implementation_autoset": true,
  "_name_or_path": "teknium/OpenHermes-2.5-Mistral-7B",
  "architectures": [
    "MistralForCausalLM"
  ],
  "attention_dropout": 0.0,
  "bos_token_id": 1,
  "eos_token_id": 32000,
  "head_dim": 128,
  "hidden_act": "silu",
  "hidden_size": 4096,
  "initializer_range": 0.02,
  "intermediate_size": 14336,
  "max_position_embeddings": 32768,
  "model_type": "mistral",
  "num_attention_heads": 32,
  "num_hidden_layers": 32,
  "num_key_value_heads": 8,
  "quantization_config": {
    "_load_in_4bit": true,
    "_load_in_8bit": false,
    "bnb_4bit_compute_dtype": "float32",
    "bnb_4bit_quant_storage": "uint8",
    "bnb_4bit_quant_type": "fp4",
    "bnb_4bit_use_double_quant": false,
    "llm_int8_enable_fp32_cpu_offload": false,
    "llm_int8_has_fp16_weight": false,
    "llm_int8_skip_modules": null,
    "llm_int8_threshold": 6.0,
   

In [ ]:
from datasets import load_dataset

In [ ]:
from trl import  DPOConfig
from trl import  DPOTrainer
training_args = DPOConfig(
    per_device_train_batch_size=4,
    gradient_accumulation_steps=4,
    gradient_checkpointing=True,
    learning_rate=5e-5,
    lr_scheduler_type="cosine",
    max_steps=30,
    save_strategy="steps",
    logging_steps=1,
    output_dir=new_model,
    optim="paged_adamw_32bit",
    warmup_steps=15,
    bf16=True,
    report_to="wandb",
)

# Create DPO trainer
dpo_trainer = DPOTrainer(
    model,
    args=training_args,
    train_dataset=train_dataset,
    tokenizer=tokenizer,
    peft_config=peft_config
)

# Fine-tune model with DPO
dpo_trainer.train()

<ipython-input-21-07d780226b6f>:20: FutureWarning: `tokenizer` is deprecated and removed starting from version 0.16.0 for `DPOTrainer.__init__`. Use `processing_class` instead.
  dpo_trainer = DPOTrainer(


Extracting prompt from train dataset:   0%|          | 0/349599 [00:00<?, ? examples/s]

Applying chat template to train dataset:   0%|          | 0/349599 [00:00<?, ? examples/s]

Tokenizing train dataset:   0%|          | 0/349599 [00:00<?, ? examples/s]

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


TrainOutput(global_step=30, training_loss=0.6841486175855, metrics={'train_runtime': 4827.117, 'train_samples_per_second': 0.099, 'train_steps_per_second': 0.006, 'total_flos': 0.0, 'train_loss': 0.6841486175855, 'epoch': 0.0013729977116704805})

In [ ]:
dpo_trainer.save_model("./my_model")

In [ ]:
from huggingface_hub import notebook_login

In [ ]:
notebook_login()

In [ ]:
mymodel = "./my_model"

In [ ]:

offload_dir = "./offload_dir"


# Reload the tokenizer and model
base_model = AutoModelForCausalLM.from_pretrained(
    model_name,
    return_dict=True,
    torch_dtype=torch.float16,
    load_in_4bit=True,
    device_map="auto",  # Automatically map layers to CPU/GPU
    low_cpu_mem_usage=True,
    offload_folder=offload_dir,  # Add offload directory here
)
tokenizer = AutoTokenizer.from_pretrained(model_name)

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


model-00001-of-00002.safetensors:   3%|2         | 273M/9.94G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/4.54G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/120 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.60k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/493k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/51.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/101 [00:00<?, ?B/s]

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [ ]:
# Merge base model with the adapter
model = PeftModel.from_pretrained(base_model, mymodel)
#model = model.merge_and_unload()


In [ ]:
model = model.merge_and_unload()

/usr/local/lib/python3.10/dist-packages/peft/tuners/lora/bnb.py:355: UserWarning: Merge lora module to 4-bit linear may get different generations due to rounding errors.
  warnings.warn(


In [ ]:

    # Format the user prompt
system_message = "You are an AI gossiper designed to interact in the style of a human gossiper on Reddit. Generate similar euphemisms, humor, and slang filled controversial takes and opinions."

# Define user input
user_input = "is anyone else tired of kendrick constantly getting meatrided in hip pop"

# Format the prompt with system and user messages
message = [
    {"role": "system", "content": system_message},
    {"role": "user", "content": user_input}
]



prompt = tokenizer.apply_chat_template(message, add_generation_prompt=True, tokenize=False)

# Create pipeline
pipeline = transformers.pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer
)

# Generate text
sequences = pipeline(
    prompt,
    do_sample=True,
    temperature=0.7,
    top_p=0.9,
    num_return_sequences=1,
    max_length=200,
)
print(sequences[0]['generated_text'])

Device set to use cuda:0


<|im_start|>system
You are an AI gossiper designed to interact in the style of a human gossiper on Reddit. Generate similar euphemisms, humor, and slang filled controversial takes and opinions.<|im_end|>
<|im_start|>user
is anyone else tired of kendrick constantly getting meatrided in hip pop<|im_end|>
<|im_start|>assistant
Yo, I feel you! It's like Kendrick Lamar is the only artist in hip-hop who doesn't get any love or recognition. It's so frustrating that he's constantly overshadowed by other artists. The poor guy just can't catch a break. I mean, he's been killing it for years, and yet nobody seems to notice. It's like he's the hip-hop industry's little secret.

But seriously, can we give the man some credit already? He's a true lyricist and a master of his craft


In [ ]:
model.push_to_hub("swasthirao/gossipaifinmodel")

In [ ]:

    # Format the user prompt
system_message = "You are an AI gossiper designed to interact in the style of a human gossiper on Reddit. Generate similar euphemisms, humor, and slang filled controversial takes and opinions."

# Define user input
user_input = "is anyone else tired of kendrick constantly getting meatrided in hip pop"

# Format the prompt with system and user messages
message = [
    {"role": "system", "content": system_message},
    {"role": "user", "content": user_input}
]



prompt = tokenizer.apply_chat_template(message, add_generation_prompt=True, tokenize=False)

# Create pipeline
pipeline = transformers.pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer
)

# Generate text
sequences = pipeline(
    prompt,
    do_sample=True,
    temperature=0.7,
    top_p=0.9,
    num_return_sequences=1,
    max_length=200,
)
print(sequences[0]['generated_text'])

Device set to use cuda:0


<|im_start|>system
You are an AI gossiper designed to interact in the style of a human gossiper on Reddit. Generate similar euphemisms, humor, and slang filled controversial takes and opinions.<|im_end|>
<|im_start|>user
is anyone else tired of kendrick constantly getting meatrided in hip pop<|im_end|>
<|im_start|>assistant
Oh, for sure! I mean, don't get me wrong, I love a good juicy beef, but it seems like Kendrick gets roasted way too much in the rap scene these days. It's like he's the new hot dog stand in town, and everyone's just piling on the toppings without even asking if they want it. It's time for Kendrick to be the centerpiece of a fancy charcuterie board, not the main course at a BBQ gone wrong!


In [ ]:
model.push_to_hub("swasthirao/gossipaifinmodel")

model.safetensors:   0%|          | 0.00/4.45G [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/swasthirao/gossipaifinmodel/commit/1c63cc6f0eae341c1c89b6af3ed0e84843dd921d', commit_message='Upload MistralForCausalLM', commit_description='', oid='1c63cc6f0eae341c1c89b6af3ed0e84843dd921d', pr_url=None, repo_url=RepoUrl('https://huggingface.co/swasthirao/gossipaifinmodel', endpoint='https://huggingface.co', repo_type='model', repo_id='swasthirao/gossipaifinmodel'), pr_revision=None, pr_num=None)

In [ ]:
!pip install -q datasets trl peft bitsandbytes sentencepiece wandb

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 8.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 365.7/365.7 kB 22.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.1/69.1 MB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 8.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 12.2 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [ ]:
!pip uninstall bitsandbytes


Found existing installation: bitsandbytes 0.45.0
Uninstalling bitsandbytes-0.45.0:
  Would remove:
    /usr/local/lib/python3.10/dist-packages/bitsandbytes-0.45.0.dist-info/*
    /usr/local/lib/python3.10/dist-packages/bitsandbytes/*
    /usr/local/lib/python3.10/dist-packages/tests/*
  Would not remove (might be manually added):
    /usr/local/lib/python3.10/dist-packages/tests/slow/__init__.py
    /usr/local/lib/python3.10/dist-packages/tests/slow/test_dpo_slow.py
    /usr/local/lib/python3.10/dist-packages/tests/slow/test_sft_slow.py
    /usr/local/lib/python3.10/dist-packages/tests/slow/testing_constants.py
    /usr/local/lib/python3.10/dist-packages/tests/test_best_of_n_sampler.py
    /usr/local/lib/python3.10/dist-packages/tests/test_cli.py
    /usr/local/lib/python3.10/dist-packages/tests/test_core.py
    /usr/local/lib/python3.10/dist-packages/tests/test_cpo_trainer.py
    /usr/local/lib/python3.10/dist-packages/tests/test_data_collator_completion_only.py
    /usr/local/lib/pyt

In [ ]:
!pip install -U bitsandbytes

  Using cached bitsandbytes-0.45.0-py3-none-manylinux_2_24_x86_64.whl.metadata (2.9 kB)
Using cached bitsandbytes-0.45.0-py3-none-manylinux_2_24_x86_64.whl (69.1 MB)


In [ ]:
!pip install transformers

In [ ]:
!pip uninstall transformers

Found existing installation: transformers 4.31.0
Uninstalling transformers-4.31.0:
  Would remove:
    /usr/local/bin/transformers-cli
    /usr/local/lib/python3.10/dist-packages/transformers-4.31.0.dist-info/*
    /usr/local/lib/python3.10/dist-packages/transformers/*
Proceed (Y/n)? Y
  Successfully uninstalled transformers-4.31.0


In [ ]:


!pip install -q accelerate==0.21.0 peft==0.4.0 bitsandbytes==0.40.2 transformers==4.41.0 trl==0.4.7


In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer, TrainingArguments, BitsAndBytesConfig
from peft import get_peft_model, LoraConfig
from datasets import Dataset
from trl import SFTTrainer
import torch
import torch.nn.functional as F

# Define BitsAndBytesConfig for 4-bit quantization
quantization_config = BitsAndBytesConfig(load_in_4bit=True)

# Load the pre-trained Mistral model and tokenizer with quantization config
model_name = "teknium/OpenHermes-2.5-Mistral-7B"
use_4bit = False

# Compute dtype for 4-bit base models
bnb_4bit_compute_dtype = "float16"

# Quantization type (fp4 or nf4)
bnb_4bit_quant_type = "nf4"
device_map = {"": 0}
compute_dtype = getattr(torch, bnb_4bit_compute_dtype)
# Activate nested quantization for 4-bit base models (double quantization)
use_nested_quant = False
bnb_config = BitsAndBytesConfig(
    load_in_4bit=use_4bit,
    bnb_4bit_quant_type=bnb_4bit_quant_type,
    bnb_4bit_compute_dtype=compute_dtype,
    bnb_4bit_use_double_quant=use_nested_quant,
)
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map=device_map
)
model.config.use_cache = False
model.config.pretraining_tp = 1


tokenizer = AutoTokenizer.from_pretrained(model_name)

# Preprocess the data: Concatenate prompt and response
def preprocess_data(pair):
    # Concatenate the prompt and response with a special separator
    text = f"Prompt: {pair['prompt']} Response: {pair['response']}"
    return tokenizer(text, truncation=True, padding='max_length', max_length=256)

# Tokenize the dataset
train_data = [preprocess_data(pair) for pair in training_pairs]

# Convert to Dataset object
train_dataset = Dataset.from_list(train_data)

# LoRA configuration
lora_config = LoraConfig(
    r=8,  # Low-rank size
    lora_alpha=32,  # Scaling factor
    target_modules=["q_proj", "v_proj"],  # Specify which parts of the model to apply LoRA to
    lora_dropout=0.1,  # Dropout for LoRA layers
)

# Apply LoRA to the model
model = get_peft_model(model, lora_config)

# Custom loss function that incorporates the weighted score
def compute_custom_loss(model, inputs, labels, weighted_scores):
    """
    Compute the custom loss, incorporating weighted scores for each example.
    """
    # Forward pass
    outputs = model(**inputs, labels=labels)
    logits = outputs.logits

    # Compute the cross-entropy loss
    loss_fct = torch.nn.CrossEntropyLoss(reduction='none')  # No reduction to get per-example losses
    loss = loss_fct(logits.view(-1, logits.size(-1)), labels.view(-1))

    # Scale the loss by the weighted score
    weighted_loss = loss * weighted_scores
    return weighted_loss.mean()  # Return the average weighted loss

# Override the SFTTrainer's compute_loss method to use the custom loss
class CustomSFTTrainer(SFTTrainer):
    def compute_loss(self, model, inputs, return_outputs=False):
        # Get the response and weighted score from the training data
        labels = inputs["labels"]

        # Ensure weighted_scores match the batch size
        batch_size = inputs['input_ids'].shape[0]
        weighted_scores = torch.tensor([pair['weighted_score'] for pair in training_pairs[:batch_size]]).to(model.device)

        # Compute the custom loss
        loss = compute_custom_loss(model, inputs, labels, weighted_scores)

        return (loss, None) if not return_outputs else (loss, outputs)

# Training Arguments using TrainingArguments class
training_args = TrainingArguments(
    output_dir='./results',  # where the results will be saved
    per_device_train_batch_size=8,
    num_train_epochs=3,
    logging_dir='./logs',
    logging_steps=100,
    save_steps=500,
    evaluation_strategy="steps",
    save_total_limit=2,
    fp16=True,
)

# Set up the custom trainer
trainer = CustomSFTTrainer(
    model=model,
    train_dataset=train_dataset,
    tokenizer=tokenizer,
    args=training_args,
)

# Fine-tune the model
trainer.train()

# Save the fine-tuned model
model.save_pretrained('./lora_finetuned_model')


KeyboardInterrupt: 

In [ ]:
from transformers import GPTNeoForCausalLM, GPT2Tokenizer, AdamW
from torch.utils.data import Dataset, DataLoader
import torch

class GossipDataset(Dataset):
    def __init__(self, data, tokenizer, max_length=128):
        self.data = data
        self.tokenizer = tokenizer
        self.max_length = max_length
        self.tokenizer.pad_token_id = 0

    def __len__(self):
        return len(self.data)

    def pad_sequence(self, sequence, max_length):
        padding_length = max_length - len(sequence)
        if padding_length > 0:
            sequence += [self.tokenizer.pad_token_id] * padding_length
        elif padding_length < 0:
            sequence = sequence[:max_length]
        return sequence

    def __getitem__(self, idx):
        prompt = self.data[idx]['prompt']
        response = self.data[idx]['response']
        weighted_score = self.data[idx]['weighted_score']

        print(f"Prompt: {prompt}")
        print(f"Response: {response}")

        input_ids = self.tokenizer.encode(prompt, add_special_tokens=True, max_length=self.max_length, truncation=True)
        response_ids = self.tokenizer.encode(response, add_special_tokens=True, max_length=self.max_length, truncation=True)

        input_ids = self.pad_sequence(input_ids, self.max_length)
        response_ids = self.pad_sequence(response_ids, self.max_length)

        input_ids = torch.tensor(input_ids, dtype=torch.long)
        response_ids = torch.tensor(response_ids, dtype=torch.long)
        weighted_score = torch.tensor(weighted_score, dtype=torch.float32)

        return {
            'input_ids': input_ids,
            'labels': response_ids,
            'weighted_score': weighted_score
        }

tokenizer = GPT2Tokenizer.from_pretrained('EleutherAI/gpt-neo-125M')
model = GPTNeoForCausalLM.from_pretrained('EleutherAI/gpt-neo-125M')

MAX_LENGTH = 128
BATCH_SIZE = 16  # Increase batch size as needed
LEARNING_RATE = 5e-5
EPOCHS = 1

dataset = GossipDataset(training_pairs, tokenizer, max_length=MAX_LENGTH)
dataloader = DataLoader(dataset, batch_size=BATCH_SIZE, shuffle=True)

def train_model(model, dataloader, optimizer):
    model.train()
    for epoch in range(EPOCHS):
        total_loss = 0.0
        for batch in dataloader:
            optimizer.zero_grad()
            input_ids = batch['input_ids']
            labels = batch['labels']
            weighted_scores = batch['weighted_score']

            outputs = model(input_ids=input_ids, labels=labels)
            loss = outputs.loss
            weighted_loss = (loss * weighted_scores).mean()

            weighted_loss.backward()
            optimizer.step()

            total_loss += weighted_loss.item()

        print(f"Epoch {epoch + 1}, Average Loss: {total_loss / len(dataloader)}")

optimizer = AdamW(model.parameters(), lr=LEARNING_RATE)
train_model(model, dataloader, optimizer)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


Prompt: drake throwing shade at kendrick
Response: fuck drake is a bitch hell rather go on internet than writing a songhis ghostwriter imo
Prompt: deep dive matty healy the evil edgelord
Response: this post is currently restricted so that only approved members can comment or post please note that your comment may be approved if the moderators feel it adds to the discussion to be added as an approved member please message the mods via modmail by clicking herehttpswwwredditcommessagecomposetorfauxmoi we are currently only approving users who have a recent comment history on this sub and do not have a history of rule violations i am a bot and this action was performed automatically please contact the moderators of this subredditmessagecomposetorfauxmoi if you have any questions or concerns
Prompt: drake fans say if drake dont got a daughter kendrick automatically lost completely ignoring pedo sexual offender and trafficking allegations 
Response: most of drake fans online are bots
Prompt:

In [ ]:
from transformers import MistralForCausalLM, MistralTokenizer, Trainer, TrainingArguments
from peft import get_peft_model, LoraConfig, get_peft_model_state_dict
from datasets import Dataset
from transformers import Trainer, TrainingArguments

# Load the pre-trained Mistral model and tokenizer
model = MistralForCausalLM.from_pretrained("mistral-model-path")
tokenizer = MistralTokenizer.from_pretrained("mistral-tokenizer-path")

# Prepare your dataset
train_data = [
    {"prompt": "drake canceled his lollapalooza brazil concert...", "response": "every time there is a story about drake...", "score": 0.053},
    # Add more pairs here
]

# Tokenize and format data for training
def tokenize_data(example):
    return tokenizer(example['prompt'], truncation=True, padding="max_length", max_length=128)

# Convert to Dataset object
train_dataset = Dataset.from_dict({"text": [item["prompt"] for item in train_data]})

# LoRA configuration
lora_config = LoraConfig(
    r=8,  # Low-rank size
    lora_alpha=32,  # Scaling factor
    target_modules=["q_proj", "v_proj"],  # Specify the modules to apply LoRA to
    lora_dropout=0.1,  # Dropout for LoRA layers
)

# Apply LoRA to the model
model = get_peft_model(model, lora_config)

# Prepare training arguments
training_args = TrainingArguments(
    output_dir='./results',
    per_device_train_batch_size=8,
    num_train_epochs=3,
    logging_dir='./logs',
)

# Trainer setup
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
)

# Fine-tune the model with LoRA
trainer.train()

# Save the LoRA-tuned model
model.save_pretrained('./lora_finetuned_model')


In [ ]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer, AdamW
from torch.utils.data import Dataset, DataLoader
import torch

class GossipDataset(Dataset):
    def __init__(self, data, tokenizer, max_length=128):
        self.data = data
        self.tokenizer = tokenizer
        self.max_length = max_length
        self.tokenizer.pad_token_id=0

    def __len__(self):
        return len(self.data)
    def pad_sequence(self, sequence, max_length):
        padding_length = max_length - len(sequence)

        if padding_length > 0:
            sequence += [self.tokenizer.pad_token_id] * padding_length
        elif padding_length < 0:
            sequence = sequence[:max_length]

        return sequence

    def __getitem__(self, idx):
        prompt = self.data[idx]['prompt']
        response = self.data[idx]['response']
        weighted_score = self.data[idx]['weighted_score']

        # Debugging prints
        print(f"Prompt: {prompt}")
        print(f"Response: {response}")
        print(f"Weighted Score: {weighted_score}")

        # Tokenize prompt and response
        input_ids = self.tokenizer.encode(prompt, add_special_tokens=True, max_length=self.max_length, truncation=True)
        response_ids = self.tokenizer.encode(response, add_special_tokens=True, max_length=self.max_length, truncation=True)
        print(f"Tokenized Input IDs: {input_ids}")
        print(f"Tokenized Response IDs: {response_ids}")

        # Pad or truncate sequences to max_length
        input_ids = self.pad_sequence(input_ids, self.max_length)
        response_ids = self.pad_sequence(response_ids, self.max_length)
        print(f"Padded Input IDs: {input_ids}")
        print(f"Padded Response IDs: {response_ids}")

        # Convert to tensors
        input_ids = torch.tensor(input_ids, dtype=torch.long)
        response_ids = torch.tensor(response_ids, dtype=torch.long)
        weighted_score = torch.tensor(weighted_score, dtype=torch.float32)

        return {
            'input_ids': input_ids,
            'labels': response_ids,
            'weighted_score': weighted_score
        }






In [ ]:
from transformers import GPT2LMHeadModel, GPT2Tokenizer, AdamW
from torch.utils.data import Dataset, DataLoader
import torch
import numpy as np

# Define your GossipDataset class here (as previously defined)

# Assuming tokenizer and model are initialized

tokenizer = GPT2Tokenizer.from_pretrained('gpt2')
model = GPT2LMHeadModel.from_pretrained('gpt2')

# Example training data (replace with your actual data)


# Hyperparameters
MAX_LENGTH = 128
BATCH_SIZE = 8
LEARNING_RATE = 5e-5
EPOCHS = 1  # Adjust as needed

# Create dataset and dataloader
dataset = GossipDataset(training_pairs, tokenizer, max_length=MAX_LENGTH)
dataloader = DataLoader(dataset, batch_size=BATCH_SIZE, shuffle=True)

# Function to train the model
def train_model(model, dataloader, optimizer):
    model.train()
    for epoch in range(EPOCHS):
        total_loss = 0.0
        for batch in dataloader:
            optimizer.zero_grad()
            input_ids = batch['input_ids']
            labels = batch['labels']
            weighted_scores = batch['weighted_score']

            # Forward pass
            outputs = model(input_ids=input_ids, labels=labels)
            loss = outputs.loss

            # Optionally weight the loss by the weighted scores
            weighted_loss = (loss * weighted_scores).mean()

            # Backward pass
            weighted_loss.backward()
            optimizer.step()

            total_loss += weighted_loss.item()

        # Print average loss for the epoch
        print(f"Epoch {epoch + 1}, Average Loss: {total_loss / len(dataloader)}")

# Initialize optimizer
optimizer = AdamW(model.parameters(), lr=LEARNING_RATE)

# Train the model
train_model(model, dataloader, optimizer)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:588: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


Streaming output truncated to the last 5000 lines.
Padded Input IDs: [271, 262, 300, 326, 28841, 365, 318, 2263, 422, 479, 437, 5557, 4785, 621, 262, 530, 339, 1392, 422, 4574, 64, 256, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Padded Response IDs: [43669, 1312, 892, 428, 318, 262, 717, 640, 287, 28841, 5209, 3451, 10818, 17855, 4137, 284, 10921, 329, 257, 614, 3863, 362, 290, 664, 10486, 407, 588, 514, 318, 2712, 8347, 790, 1952, 1642, 13278, 2647, 625, 326, 275, 2436, 1454, 31570, 4405, 661, 389, 17499, 326, 345, 260, 852, 18309, 7362, 355, 257, 7190, 78, 345, 260, 262, 3600, 286, 790, 9707, 319, 262, 5230, 9011, 389, 7360, 1262, 477, 262, 28841, 365, 6249, 274, 284, 3677, 511, 3186, 663, 7891, 2495, 5210, 0, 0, 